In [1]:
import polars as pl
import plotly.graph_objects as go
import plotly.express as px
import re
import os
import pandas as pd

In [2]:
folder_path = "../data/parquet_files"
files = [os.path.join(folder_path, f) for f in os.listdir(folder_path) if f.endswith('.parquet')]

data_frames = [pl.read_parquet(file) for file in files]
combined_df = pl.concat(data_frames)

In [3]:
def add_prediction_column(df):
    """Add a prediction column based on the score threshold of 0.5."""
    return df.with_columns((df['score'] > 0.5).cast(pl.Int8).alias('prediction'))

def add_threshold_columns(df, threshold):
    return df.with_columns((df['score'] > threshold).cast(pl.Int8).alias(f'threshold_{str(threshold)}'))

combined_df = add_prediction_column(combined_df)
combined_df = add_threshold_columns(combined_df, 0.5)
combined_df = add_threshold_columns(combined_df, 0.9)

In [4]:
def add_cell_line_run_column(df):
    df = df.with_columns((pl.col("cell_line") + "_" + pl.col("run")).alias("cell_line_run"))
    return df

combined_df = add_cell_line_run_column(combined_df)

In [5]:
print(combined_df.columns)

['cell_line', 'run', 'transcript_id', 'transcript_position', 'sequence', 'proportion_1', 'proportion_2', 'proportion_3', 'diff_1_1', 'diff_1_2', 'diff_1_3', 'diff_2_1', 'diff_2_2', 'diff_2_3', 'length', 'mean_0', 'var_0', 'max_0', 'min_0', 'mean_1', 'var_1', 'max_1', 'min_1', 'mean_2', 'var_2', 'max_2', 'min_2', 'mean_3', 'var_3', 'max_3', 'min_3', 'mean_4', 'var_4', 'max_4', 'min_4', 'mean_5', 'var_5', 'max_5', 'min_5', 'mean_6', 'var_6', 'max_6', 'min_6', 'mean_7', 'var_7', 'max_7', 'min_7', 'mean_8', 'var_8', 'max_8', 'min_8', 'score', 'prediction', 'threshold_0.5', 'threshold_0.9', 'cell_line_run']


In [6]:
print(combined_df[0:5])

shape: (5, 56)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ cell_line ┆ run       ┆ transcrip ┆ transcrip ┆ … ┆ predictio ┆ threshold ┆ threshold ┆ cell_lin │
│ ---       ┆ ---       ┆ t_id      ┆ t_positio ┆   ┆ n         ┆ _0.5      ┆ _0.9      ┆ e_run    │
│ str       ┆ str       ┆ ---       ┆ n         ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---      │
│           ┆           ┆ str       ┆ ---       ┆   ┆ i8        ┆ i8        ┆ i8        ┆ str      │
│           ┆           ┆           ┆ i64       ┆   ┆           ┆           ┆           ┆          │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ A549      ┆ replicate ┆ ENST00000 ┆ 108       ┆ … ┆ 0         ┆ 0         ┆ 0         ┆ A549_rep │
│           ┆ 5_run1    ┆ 418539    ┆           ┆   ┆           ┆           ┆           ┆ licate5_ │
│           ┆           ┆           ┆           ┆   ┆           ┆           

In [ ]:

def calculate_prediction_counts_by_cell_line(df, position_range=(0, 250000)):
    # Filter to the specified transcript_position range
    df = df.filter((pl.col("transcript_position") >= position_range[0]) & (pl.col("transcript_position") <= position_range[1]))

    # Calculate counts and proportions of prediction == 1 and prediction == 0 for each cell line
    count_df = (
        df.group_by("cell_line")
        .agg([
            (pl.col("prediction") == 1).sum().alias("count_prediction_1"),  # Count of prediction == 1
            (pl.col("prediction") == 0).sum().alias("count_prediction_0")   # Count of prediction == 0
        ])
        .with_columns([
            (pl.col("count_prediction_1") / (pl.col("count_prediction_1") + pl.col("count_prediction_0"))).alias("proportion_prediction_1"),
            (pl.col("count_prediction_0") / (pl.col("count_prediction_1") + pl.col("count_prediction_0"))).alias("proportion_prediction_0")
        ])
        .sort("cell_line")
    )

    return count_df

def plot_prediction_counts_by_cell_line_bar(count_df):
    count_df_pandas = count_df.to_pandas()

    fig = go.Figure()

    colors = {
        "modifications": "rgb(255, 127, 14)",  # orange for mods
        "non_modifications": "rgb(31, 119, 180)"  # Blue for non-modifications 
    }

    # Add bar for prediction == 1 (modifications) with count and proportion
    fig.add_trace(go.Bar(
        x=count_df_pandas["cell_line"],
        y=count_df_pandas["count_prediction_1"],
        name="Modifications (Prediction=1)",
        marker_color=colors["modifications"],
        text=(count_df_pandas["count_prediction_1"].astype(str) + " (" +
              (count_df_pandas["proportion_prediction_1"] * 100).round(2).astype(str) + '%)'),
        textposition="outside"
    ))

    # Add bar for prediction == 0 (non-modifications) with count and proportion
    fig.add_trace(go.Bar(
        x=count_df_pandas["cell_line"],
        y=count_df_pandas["count_prediction_0"],
        name="Non-Modifications (Prediction=0)",
        marker_color=colors["non_modifications"],
        text=(count_df_pandas["count_prediction_0"].astype(str) + " (" +
              (count_df_pandas["proportion_prediction_0"] * 100).round(2).astype(str) + '%)'),
        textposition="outside"
    ))

    # Update layout to make it a grouped bar chart
    fig.update_layout(
        title={
            "text": "Counts and Proportions of Modifications and Non-Modifications across Cell Lines",
            "xanchor": 'center',
            "x": 0.5
        },
        xaxis_title="Cell Line",
        yaxis_title="Counts",
        barmode="group",  
        legend_title="Modification Type",
        plot_bgcolor="white"  
    )

    fig.show()

count_df = calculate_prediction_counts_by_cell_line(combined_df)
plot_prediction_counts_by_cell_line_bar(count_df)


### Correlations between Cell Lines

Am not too clear on the correlation calculations but it should resolve positions which other lines/runs do not have data on by ignoring it ie. if run A has position 244 but run B does not, I think it ignores

Also there is for some reason duplicate transcript_positions which I am quite confused about

In [6]:
def prepare_correlation_data(df):
    
    # Aggregate by taking the mean prediction for each transcript_position and cell_line_run combination
    # Extra step to handle duplicate positions? - for some reason there are duplicates
    aggregated_df = (
        df.group_by(["transcript_position", "cell_line_run"])
        .agg(pl.col("prediction").mean().alias("mean_prediction"))
    )
    
    pivot_df = (
        aggregated_df.to_pandas()
        .pivot(index="transcript_position", columns="cell_line_run", values="mean_prediction")
        .fillna(0) 
    )

    correlation_matrix = pivot_df.corr()

    return correlation_matrix

def plot_correlation_heatmap(correlation_matrix, maxz, minz):
    fig = go.Figure(
        data=go.Heatmap(
            z=correlation_matrix.values,
            x=correlation_matrix.columns,
            y=correlation_matrix.index,
            colorscale=px.colors.diverging.RdBu,
            colorbar=dict(title="Correlation Coefficient"),
            zmin=minz,
            zmax=maxz # for best effect, set this to 0.4
        )
    )

    fig.update_layout(
        title={
            "text": "Correlation Heatmap of Predictions across Cell Lines",
            "xanchor": 'center',
            "x": 0.5
        },
    )

    fig.show()

correlation_matrix = prepare_correlation_data(combined_df)
plot_correlation_heatmap(correlation_matrix, 1, -1)

In [9]:
import pandas as pd
import numpy as np

# Assuming `df` is your correlation DataFrame
df = correlation_matrix.copy()  # Make a copy if needed

# Extract cell line names from the index and columns by splitting on "_"
cell_lines = pd.Series(df.index).apply(lambda x: x.split("_")[0])
cell_line_dict = dict(zip(df.index, cell_lines))

# Initialize lists to store correlations for same and different cell lines
same_cell_line_correlations = []
different_cell_line_correlations = []

# Loop through the correlation matrix to categorize correlations
for i in range(len(df)):
    for j in range(i + 1, len(df)):  # Only consider the upper triangle to avoid duplicates
        cell_line_i = cell_line_dict[df.index[i]]
        cell_line_j = cell_line_dict[df.columns[j]]
        correlation = df.iloc[i, j]
        
        if cell_line_i == cell_line_j:
            same_cell_line_correlations.append(correlation)
        else:
            different_cell_line_correlations.append(correlation)

# Calculate the average correlation for same and different cell lines
average_same_cell_line_correlation = np.mean(same_cell_line_correlations)
average_different_cell_line_correlation = np.mean(different_cell_line_correlations)

average_same_cell_line_correlation, average_different_cell_line_correlation


(0.2741350711645967, 0.23763089855335348)

In [11]:
# Extract only the rows and columns for the "HepG2" cell line
hepg2_df = df.filter(regex="^MCF7", axis=0).filter(regex="^MCF7", axis=1)

# Calculate the mean correlation score, excluding the diagonal
hepg2_correlations = hepg2_df.where(np.triu(np.ones(hepg2_df.shape), k=1).astype(bool))
mean_hepg2_correlation = hepg2_correlations.stack().mean()

mean_hepg2_correlation


0.22533229369931138

In [7]:
plot_correlation_heatmap(correlation_matrix,0.35, 0)

### Prediction x Feature Correlations

Largely similar to the correlation heatmap

In [ ]:
def calculate_prediction_correlations(df):
    numerical_df = df.select([col for col in df.columns if df.schema[col] in [pl.Float64, pl.Int64, pl.Int8]])
    numerical_df = numerical_df.to_pandas()

    prediction_correlations = numerical_df.corr()['prediction'].drop('prediction')  # Drop self-correlation

    return prediction_correlations

def plot_prediction_correlation_heatmap(prediction_correlations):
    fig = go.Figure(
        data=go.Heatmap(
            z=prediction_correlations.values.reshape(1, -1),
            x=prediction_correlations.index,
            y=["prediction"],
            colorscale="Viridis",
            colorbar=dict(title="Correlation Coefficient")
        )
    )

    fig.update_layout(
        title="Correlation of Features with Prediction",
        xaxis_title="Features",
        yaxis_title="Prediction",
        template="plotly_dark"
    )

    fig.show()

prediction_correlations = calculate_prediction_correlations(combined_df)
plot_prediction_correlation_heatmap(prediction_correlations)

### Modification Proportions across the RNA Sequence

3 main distinct positions with the modifications

1) 0 - 30k
2) 50 - 70k
3) 90 - 100k

In [36]:
def calculate_prediction_counts(df, bin_size=1000, position_range=(0, 3000000)):
    # Filter to the specified transcript_position range
    df = df.filter((pl.col("transcript_position") >= position_range[0]) & (pl.col("transcript_position") <= position_range[1]))

    df = df.with_columns(((pl.col("transcript_position") // bin_size) * bin_size).alias("binned_position"))

    # Calculate the counts of prediction == 1 and prediction == 0
    count_df = (
        df.group_by("binned_position")
        .agg([
            (pl.col("prediction") == 1).sum().alias("count_prediction_1"),  # Count of prediction == 1
            (pl.col("prediction") == 0).sum().alias("count_prediction_0")   # Count of prediction == 0
        ])
        .sort("binned_position")
    )

    return count_df

def plot_prediction_counts(count_df):
    fig = go.Figure()

    fig.add_trace(go.Scatter(
        x=count_df["binned_position"],
        y=count_df["count_prediction_1"],
        mode="lines+markers",
        name="Count of Prediction=1",
        line=dict(color="blue")
    ))

    fig.add_trace(go.Scatter(
        x=count_df["binned_position"],
        y=count_df["count_prediction_0"],
        mode="lines+markers",
        name="Count of Prediction=0",
        line=dict(color="orange")
    ))

    fig.update_layout(
        title="Counts of Modifications across Transcript Positions",
        xaxis_title="Binned Transcript Position",
        yaxis_title="Count of Modifications",
        legend_title="Prediction",
    )

    fig.show()

count_df = calculate_prediction_counts(combined_df)
plot_prediction_counts(count_df)

In [ ]:
def calculate_prediction_proportion(df, bin_size=1000, position_range=(0, 250000)):
    # Filter to the specified transcript_position range
    df = df.filter((pl.col("transcript_position") >= position_range[0]) & (pl.col("transcript_position") <= position_range[1]))

    df = df.with_columns(((pl.col("transcript_position") // bin_size) * bin_size).alias("binned_position"))

    proportion_df = (
        df.group_by("binned_position")
        .agg([
            (pl.col("prediction") == 1).mean().alias("proportion_prediction_1")
        ])
        .sort("binned_position")
    )

    return proportion_df

def plot_prediction_proportion(proportion_df):
    fig = go.Figure(
        data=go.Scatter(
            x=proportion_df["binned_position"],
            y=proportion_df["proportion_prediction_1"],
            mode="lines+markers",
            name="Proportion of Prediction=1"
        )
    )

    fig.update_layout(
        title="Proportion of Modifications across Transcript Positions",
        xaxis_title="Binned Transcript Position",
        yaxis_title="Proportion of m6a Modifications",
    )

    fig.show()

# Example Usage
# Assuming combined_df is your Polars DataFrame with 'transcript_position' and 'prediction' columns
proportion_df = calculate_prediction_proportion(combined_df)
plot_prediction_proportion(proportion_df)

In [ ]:
def calculate_prediction_proportion_by_cell_line(df, bin_size=1000, position_range=(0, 150000)):
    df = df.filter((pl.col("transcript_position") >= position_range[0]) & (pl.col("transcript_position") <= position_range[1]))
    df = df.with_columns(((pl.col("transcript_position") // bin_size) * bin_size).alias("binned_position"))

    proportion_df = (
        df.group_by(["cell_line_run", "binned_position"])
        .agg([
            (pl.col("prediction") == 1).mean().alias("proportion_prediction_1")
        ])
        .sort(["cell_line_run", "binned_position"])
    )

    all_bins = pl.DataFrame({
        "binned_position": list(range(position_range[0], position_range[1] + bin_size, bin_size))
    })
    cell_line_runs = df.select("cell_line_run").unique()

    # Cross join to create all possible combinations of cell_line_run and binned_position
    complete_df = cell_line_runs.join(all_bins, how="cross")

    # Join with proportion_df to fill missing bins with 0
    filled_df = complete_df.join(proportion_df, on=["cell_line_run", "binned_position"], how="left").fill_null(0)

    return filled_df

def plot_prediction_proportion_by_cell_line(proportion_df):
    fig = go.Figure()

    # Convert Polars DataFrame to Pandas for Plotly compatibility
    proportion_df_pandas = proportion_df.to_pandas()

    for cell_line_run in proportion_df_pandas['cell_line_run'].unique():
        subset = proportion_df_pandas[proportion_df_pandas['cell_line_run'] == cell_line_run]
        
        fig.add_trace(
            go.Scatter(
                x=subset['binned_position'],
                y=subset['proportion_prediction_1'],
                mode="lines+markers",
                name=cell_line_run
            )
        )

    fig.update_layout(
        title="Proportion of Prediction=1 across Transcript Positions by Cell Line + Run",
        xaxis_title="Binned Transcript Position",
        yaxis_title="Proportion of Prediction=1",
        legend_title="Cell Line + Run",
        template="plotly_dark"
    )

    fig.show()

proportion_df = calculate_prediction_proportion_by_cell_line(combined_df)
plot_prediction_proportion_by_cell_line(proportion_df)

In [17]:
def calculate_prediction_proportion_by_cell_line(df, bin_size=1000, position_range=(0, 150000)):
    df = df.filter((pl.col("transcript_position") >= position_range[0]) & (pl.col("transcript_position") <= position_range[1]))
    df = df.with_columns(((pl.col("transcript_position") // bin_size) * bin_size).alias("binned_position"))

    proportion_df = (
        df.group_by(["cell_line", "binned_position"])
        .agg([
            (pl.col("prediction") == 1).mean().alias("proportion_prediction_1")
        ])
        .sort(["cell_line", "binned_position"])
    )

    all_bins = pl.DataFrame({
        "binned_position": list(range(position_range[0], position_range[1] + bin_size, bin_size))
    })
    cell_line_runs = df.select("cell_line").unique()

    complete_df = cell_line_runs.join(all_bins, how="cross")

    filled_df = complete_df.join(proportion_df, on=["cell_line", "binned_position"], how="left").fill_null(0)

    return filled_df

In [ ]:
def plot_prediction_proportion_by_cell_line(proportion_df):
    fig = go.Figure()

    # Convert Polars DataFrame to Pandas for Plotly compatibility
    proportion_df_pandas = proportion_df.to_pandas()

    # Plot each cell_line_run with a different color
    for cell_line_run in proportion_df_pandas['cell_line'].unique():
        subset = proportion_df_pandas[proportion_df_pandas['cell_line'] == cell_line_run]
        
        fig.add_trace(
            go.Scatter(
                x=subset['binned_position'],
                y=subset['proportion_prediction_1'],
                mode="lines+markers",
                name=cell_line_run
            )
        )

    fig.update_layout(
        title="Proportion of Modifications across Transcript Positions by Cell Line",
        xaxis_title="Binned Transcript Position",
        yaxis_title="Proportion of m6a Modifications",
        legend_title="Cell Line + Run",
    )

    fig.show()

proportion_df = calculate_prediction_proportion_by_cell_line(combined_df)
plot_prediction_proportion_by_cell_line(proportion_df)

Making a note here but if you look at MCF7 Cell Line versus the rest, there are 5 distinct positions where there are modifications detected where most other cell lines have 3 or max 4 positions, this corroborates the correlation between cell lines heatmap (the white and blue correlation heatmap)

In [6]:
import polars as pl

def calculate_prediction_proportion_by_cell_line_normalized(df, bin_count=100):
    # Step 1: Normalize transcript_position within each cell line
    df = df.with_columns(
        (pl.col("transcript_position") / pl.col("transcript_position").max().over("cell_line")).alias("normalized_position")
    )
    
    # Step 2: Bin the normalized values into `bin_count` bins
    df = df.with_columns(
        (pl.col("normalized_position") * bin_count).cast(int).alias("binned_normalized_position")
    )
    
    # Step 3: Calculate the proportion of predictions in each normalized bin
    proportion_df = (
        df.group_by(["cell_line", "binned_normalized_position"])
        .agg([
            (pl.col("prediction") == 1).mean().alias("proportion_prediction_1")
        ])
        .sort(["cell_line", "binned_normalized_position"])
    )

    # Generate all possible bins
    all_bins = pl.DataFrame({
        "binned_normalized_position": list(range(bin_count))
    })
    cell_line_runs = df.select("cell_line").unique()

    # Create a complete set of bins for each cell line
    complete_df = cell_line_runs.join(all_bins, how="cross")

    # Join with the calculated proportions and fill missing values with 0
    filled_df = complete_df.join(proportion_df, on=["cell_line", "binned_normalized_position"], how="left").fill_null(0)

    return filled_df


In [35]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

def plot_prediction_proportion_by_cell_line_faceted(proportion_df, x_axis='binned_normalized_position'):
    proportion_df_pandas = proportion_df.to_pandas()

    
    unique_cell_lines = proportion_df_pandas['cell_line'].unique()
    num_rows = len(unique_cell_lines)
    scientific_palette = [
        "rgb(31, 119, 180)",   # Blue
        "rgb(255, 127, 14)",   # Orange
        "rgb(44, 160, 44)",    # Green
        "rgb(214, 39, 40)",    # Red
        "rgb(148, 103, 189)",  # Purple
    ]

    fig = make_subplots(
        rows=num_rows, cols=1, 
        shared_xaxes=True, 
        vertical_spacing=0.05, 
        subplot_titles=[f"Cell Line: {cell_line}" for cell_line in unique_cell_lines]
    )

    for i, cell_line in enumerate(unique_cell_lines, start=1):
        subset = proportion_df_pandas[proportion_df_pandas['cell_line'] == cell_line]
        
        fig.add_trace(
            go.Scatter(
                x=subset[x_axis],
                y=subset['proportion_prediction_1'],
                mode="lines+markers",
                name=cell_line,
                line=dict(color=scientific_palette[i % len(scientific_palette)]),  # Assign color from palette
                marker=dict(color=scientific_palette[i % len(scientific_palette)])
            ),
            row=i, col=1
        )

        fig.update_yaxes(range=[0, 0.2], row=i, col=1)
        fig.update_xaxes(showticklabels=True, row=i, col=1)

    # Update layout for the overall figure with increased height and shared y-axis title
    fig.update_layout(
        title={
            'text': "Proportion of Modifications across Transcript Positions by Cell Line",
            'x': 0.5,  # Center the title
            'xanchor': 'center'
        },
        yaxis_title={'text': "Proportion of m6a Modifications"},  # Single y-axis title across all subplots
        height=200 * num_rows,  # Adjust height based on the number of rows
        showlegend=False,  # Hides the legend, each cell line is in a separate subplot
    )

    fig.update_xaxes(title_text="Binned Transcript Position", row=num_rows, col=1)
    
    fig.show()

# Call the modified plotting function
proportion_df_not_normalised = calculate_prediction_proportion_by_cell_line(combined_df, bin_size=50, position_range=(0,18000))
proportion_df = calculate_prediction_proportion_by_cell_line_normalized(combined_df)
plot_prediction_proportion_by_cell_line_faceted(proportion_df)
plot_prediction_proportion_by_cell_line_faceted(proportion_df_not_normalised, x_axis="binned_position")

In [40]:
import polars as pl
from plotly.subplots import make_subplots
import plotly.graph_objects as go

def calculate_modification_by_cell_line(df, metric="proportion", position_range=(0, 20000), bin_size=100):
    # Step 1: Filter the DataFrame based on the specified position range
    df = df.filter((pl.col("transcript_position") >= position_range[0]) & 
                   (pl.col("transcript_position") <= position_range[1]))
    
    # Step 2: Re-index transcript_position values to spread evenly across the x-axis
    df = df.with_columns(
        pl.col("transcript_position").rank().alias("spread_position")  # rank to create evenly spaced points
    )
    
    # Step 3: Calculate the selected metric for each cell line at each spread position
    if metric == "proportion":
        result_df = (
            df.group_by(["cell_line", "spread_position"])
            .agg([
                (pl.col("prediction") == 1).mean().alias("metric_value")  # Proportion of modifications
            ])
            .sort(["cell_line", "spread_position"])
        )
    elif metric == "density":
        # Calculate density over bins of spread positions
        result_df = (
            df.with_columns(
                ((pl.col("spread_position") // bin_size) * bin_size).alias("binned_position")
            )
            .group_by(["cell_line", "binned_position"])
            .agg([
                (pl.col("prediction") == 1).sum().alias("metric_value")  # Sum to count m6A sites in each bin
            ])
            .sort(["cell_line", "binned_position"])
        )

    return result_df

def plot_modification_by_cell_line(result_df, metric="proportion"):
    result_df_pandas = result_df.to_pandas()
    
    unique_cell_lines = result_df_pandas['cell_line'].unique()
    num_rows = len(unique_cell_lines)
    scientific_palette = [
        "rgb(31, 119, 180)",   # Blue
        "rgb(255, 127, 14)",   # Orange
        "rgb(44, 160, 44)",    # Green
        "rgb(214, 39, 40)",    # Red
        "rgb(148, 103, 189)",  # Purple
    ]

    fig = make_subplots(
        rows=num_rows, cols=1, 
        shared_xaxes=True, 
        vertical_spacing=0.05, 
        subplot_titles=[f"Cell Line: {cell_line}" for cell_line in unique_cell_lines]
    )

    x_axis_column = "spread_position" if metric == "proportion" else "binned_position"

    for i, cell_line in enumerate(unique_cell_lines, start=1):
        subset = result_df_pandas[result_df_pandas['cell_line'] == cell_line]
        
        fig.add_trace(
            go.Scatter(
                x=subset[x_axis_column],
                y=subset['metric_value'],
                mode="lines+markers",
                name=cell_line,
                line=dict(color=scientific_palette[i % len(scientific_palette)]),
                marker=dict(color=scientific_palette[i % len(scientific_palette)])
            ),
            row=i, col=1
        )

        fig.update_yaxes(range=[0, 1.1] if metric == "proportion" else None, row=i, col=1)
        fig.update_xaxes(showticklabels=True, row=i, col=1)

    # Update layout for the overall figure with an appropriate y-axis label and title
    fig.update_layout(
        title={
            'text': f"{metric.capitalize()} of Modifications across Spread Transcript Positions by Cell Line",
            'x': 0.5,
            'xanchor': 'center'
        },
        yaxis_title={'text': f"{'Proportion of m6A Modifications' if metric == 'proportion' else 'Density of m6A Modifications'}"},
        height=200 * num_rows,
        showlegend=False,
    )

    fig.update_xaxes(title_text="Spread Transcript Position", row=num_rows, col=1)
    
    fig.show()

# Example usage:
result_df = calculate_modification_by_cell_line(combined_df, metric="proportion", position_range=(0, 205000), bin_size=2500)
plot_modification_by_cell_line(result_df, metric="proportion")


In [55]:
import polars as pl
from plotly.subplots import make_subplots
import plotly.graph_objects as go

def calculate_modification_by_cell_line(df, metric="proportion", position_range=(0, 20000), bin_size=100):
    # Step 1: Filter the DataFrame based on the specified position range
    df = df.filter((pl.col("transcript_position") >= position_range[0]) & 
                   (pl.col("transcript_position") <= position_range[1]))
    
    # Step 2: Aggregate by cell_line and transcript_position to calculate the proportion of modifications
    df = (
        df.group_by(["cell_line", "transcript_position"])
        .agg([
            (pl.col("prediction") == 1).mean().alias("proportion_prediction_1")  # Calculate proportion of modifications
        ])
    )
    
    # Step 3: Rank unique transcript positions to create spread positions
    df = df.with_columns(
        pl.col("transcript_position").rank().alias("spread_position")  # rank to create evenly spaced points
    )
    
    # Step 4: Calculate the selected metric for each cell line at each spread position
    if metric == "proportion":
        # We already have the proportions, so we just rename the column
        result_df = df.rename({"proportion_prediction_1": "metric_value"}).sort(["cell_line", "spread_position"])
    elif metric == "density":
        # Calculate density over bins of spread positions
        result_df = (
            df.with_columns(
                ((pl.col("spread_position") // bin_size) * bin_size).alias("binned_position")
            )
            .group_by(["cell_line", "binned_position"])
            .agg([
                pl.col("proportion_prediction_1").sum().alias("metric_value")  # Sum to count m6A sites in each bin
            ])
            .sort(["cell_line", "binned_position"])
        )

    return result_df

def plot_modification_by_cell_line(result_df, metric="proportion"):
    result_df_pandas = result_df.to_pandas()
    
    unique_cell_lines = result_df_pandas['cell_line'].unique()
    num_rows = len(unique_cell_lines)
    scientific_palette = [
        "rgb(31, 119, 180)",   # Blue
        "rgb(255, 127, 14)",   # Orange
        "rgb(44, 160, 44)",    # Green
        "rgb(214, 39, 40)",    # Red
        "rgb(148, 103, 189)",  # Purple
    ]

    fig = make_subplots(
        rows=num_rows, cols=1, 
        shared_xaxes=True, 
        vertical_spacing=0.05, 
        subplot_titles=[f"Cell Line: {cell_line}" for cell_line in unique_cell_lines]
    )

    x_axis_column = "spread_position" if metric == "proportion" else "binned_position"

    for i, cell_line in enumerate(unique_cell_lines, start=1):
        subset = result_df_pandas[result_df_pandas['cell_line'] == cell_line]
        
        fig.add_trace(
            go.Scatter(
                x=subset[x_axis_column],
                y=subset['metric_value'],
                mode="lines+markers",
                name=cell_line,
                line=dict(color=scientific_palette[i % len(scientific_palette)]),
                marker=dict(color=scientific_palette[i % len(scientific_palette)])
            ),
            row=i, col=1
        )

        fig.update_yaxes(range=[0, 1.1] if metric == "proportion" else None, row=i, col=1)
        fig.update_xaxes(showticklabels=True, row=i, col=1)

    # Update layout for the overall figure with an appropriate y-axis label and title
    fig.update_layout(
        title={
            'text': f"{metric.capitalize()} of Modifications across Spread Transcript Positions by Cell Line",
            'x': 0.5,
            'xanchor': 'center'
        },
        yaxis_title={'text': f"{'Proportion of m6A Modifications' if metric == 'proportion' else 'Density of m6A Modifications'}"},
        height=200 * num_rows,
        showlegend=False,
    )

    fig.update_xaxes(title_text="Spread Transcript Position", row=num_rows, col=1)
    
    fig.show()

# Example usage:
result_df = calculate_modification_by_cell_line(combined_df, metric="density", position_range=(0, 205000), bin_size=150)
plot_modification_by_cell_line(result_df, metric="density")


In [107]:
# adding moving average
import polars as pl
from plotly.subplots import make_subplots
import plotly.graph_objects as go

def calculate_modification_by_cell_line(df, metric="proportion", position_range=(0, 20000), bin_size=100):
    # Step 1: Filter the DataFrame based on the specified position range
    df = df.filter((pl.col("transcript_position") >= position_range[0]) & 
                   (pl.col("transcript_position") <= position_range[1]))
    
    # Step 2: Aggregate by cell_line and transcript_position to calculate the proportion of modifications
    df = (
        df.group_by(["cell_line", "transcript_position"])
        .agg([
            (pl.col("prediction") == 1).mean().alias("proportion_prediction_1")  # Calculate proportion of modifications
        ])
    )
    
    # Step 3: Rank unique transcript positions to create spread positions
    df = df.with_columns(
        pl.col("transcript_position").rank().alias("spread_position")  # rank to create evenly spaced points
    )
    
    # Step 4: Calculate the selected metric for each cell line at each spread position
    if metric == "proportion":
        # We already have the proportions, so we just rename the column
        result_df = df.rename({"proportion_prediction_1": "metric_value"}).sort(["cell_line", "spread_position"])
    elif metric == "density":
        # Calculate density over bins of spread positions
        result_df = (
            df.with_columns(
                ((pl.col("spread_position") // bin_size) * bin_size).alias("binned_position")
            )
            .group_by(["cell_line", "binned_position"])
            .agg([
                pl.col("proportion_prediction_1").sum().alias("metric_value")  # Sum to count m6A sites in each bin
            ])
            .sort(["cell_line", "binned_position"])
        )

    return result_df

def plot_modification_by_cell_line(result_df, metric="proportion", apply_moving_average=False, window_size=5):
    result_df_pandas = result_df.to_pandas()
    
    unique_cell_lines = result_df_pandas['cell_line'].unique()
    num_rows = len(unique_cell_lines)
    scientific_palette = [
        "rgb(31, 119, 180)",   # Blue
        "rgb(255, 127, 14)",   # Orange
        "rgb(44, 160, 44)",    # Green
        "rgb(214, 39, 40)",    # Red
        "rgb(148, 103, 189)",  # Purple
    ]

    fig = make_subplots(
        rows=num_rows, cols=1, 
        shared_xaxes=True, 
        vertical_spacing=0.05, 
        subplot_titles=[f"Cell Line: {cell_line}" for cell_line in unique_cell_lines]
    )

    x_axis_column = "spread_position" if metric == "proportion" else "binned_position"

    for i, cell_line in enumerate(unique_cell_lines, start=1):
        subset = result_df_pandas[result_df_pandas['cell_line'] == cell_line]
        
        # Apply moving average if specified
        y_values = subset['metric_value']
        if apply_moving_average:
            y_values = y_values.rolling(window=window_size, min_periods=1).mean()
        
        fig.add_trace(
            go.Scatter(
                x=subset[x_axis_column],
                y=y_values,
                mode="lines+markers",
                name=cell_line,
                line=dict(color=scientific_palette[i % len(scientific_palette)]),
                marker=dict(color=scientific_palette[i % len(scientific_palette)])
            ),
            row=i, col=1
        )

        fig.update_yaxes(range=[0, 0.55] if metric == "proportion" else None, row=i, col=1)
        fig.update_xaxes(showticklabels=True, row=i, col=1)

    # Update layout for the overall figure with an appropriate y-axis label and title
    fig.update_layout(
        title={
            'text': f"{metric.capitalize()} of Modifications across Spread Transcript Positions by Cell Line",
            'x': 0.5,
            'xanchor': 'center'
        },
        yaxis_title={'text': f"{'Proportion of m6A Modifications' if metric == 'proportion' else 'Density of m6A Modifications'}"},
        height=200 * num_rows,
        showlegend=False,
    )

    fig.update_xaxes(title_text="Spread Transcript Position", row=num_rows, col=1)
    
    fig.show()

# Example usage:
result_df = calculate_modification_by_cell_line(combined_df, metric="proportion", position_range=(0, 220000), bin_size=500)
plot_modification_by_cell_line(result_df, metric="proportion", apply_moving_average=True, window_size=6)


In [45]:
print(combined_df.columns)

['cell_line', 'run', 'transcript_id', 'transcript_position', 'sequence', 'proportion_1', 'proportion_2', 'proportion_3', 'diff_1_1', 'diff_1_2', 'diff_1_3', 'diff_2_1', 'diff_2_2', 'diff_2_3', 'length', 'mean_0', 'var_0', 'max_0', 'min_0', 'mean_1', 'var_1', 'max_1', 'min_1', 'mean_2', 'var_2', 'max_2', 'min_2', 'mean_3', 'var_3', 'max_3', 'min_3', 'mean_4', 'var_4', 'max_4', 'min_4', 'mean_5', 'var_5', 'max_5', 'min_5', 'mean_6', 'var_6', 'max_6', 'min_6', 'mean_7', 'var_7', 'max_7', 'min_7', 'mean_8', 'var_8', 'max_8', 'min_8', 'score', 'prediction', 'threshold_0.5', 'threshold_0.9', 'cell_line_run']


In [8]:
def find_common_transcript_ids(df):
    common_transcripts = (
        df.group_by("transcript_id")
        .agg([
            pl.col("cell_line").n_unique().alias("cell_line_count"),  
            pl.col("cell_line").unique().alias("unique_cell_lines")   
        ])
        .filter(pl.col("cell_line_count") > 1) 
    )

    return common_transcripts.select(["transcript_id", "unique_cell_lines"])

common_transcripts = find_common_transcript_ids(combined_df)
print(common_transcripts)


shape: (59_354, 2)
┌─────────────────┬───────────────────────────────┐
│ transcript_id   ┆ unique_cell_lines             │
│ ---             ┆ ---                           │
│ str             ┆ list[str]                     │
╞═════════════════╪═══════════════════════════════╡
│ ENST00000565873 ┆ ["A549", "MCF7", … "K562"]    │
│ ENST00000509437 ┆ ["MCF7", "K562", … "A549"]    │
│ ENST00000309060 ┆ ["Hct116", "HepG2", … "A549"] │
│ ENST00000529422 ┆ ["MCF7", "HepG2", … "Hct116"] │
│ ENST00000397961 ┆ ["HepG2", "A549", … "K562"]   │
│ …               ┆ …                             │
│ ENST00000374867 ┆ ["Hct116", "HepG2", "A549"]   │
│ ENST00000555235 ┆ ["HepG2", "Hct116", … "A549"] │
│ ENST00000546959 ┆ ["A549", "K562", … "Hct116"]  │
│ ENST00000372003 ┆ ["HepG2", "Hct116", … "MCF7"] │
│ ENST00000501280 ┆ ["Hct116", "K562", "HepG2"]   │
└─────────────────┴───────────────────────────────┘


In [11]:
common_transcripts = find_common_transcript_ids(combined_df)
filtered_df = combined_df.join(common_transcripts, on="transcript_id", how="inner")

proportion_df = calculate_prediction_proportion_by_cell_line(filtered_df)
plot_prediction_proportion_by_cell_line(proportion_df)

### Sequences


In [13]:
unique_sequences = combined_df['sequence'].unique()
unique_sequences
print(len(unique_sequences))

288


In [15]:
result_df = (
    combined_df.group_by("sequence")
    .agg([
        (pl.col("prediction") == 1).sum().alias("count_prediction_1"),  # Count of prediction == 1
        (pl.col("prediction") == 0).sum().alias("count_prediction_0"),  # Count of prediction == 0
    ])
    .with_columns([
        (pl.col("count_prediction_1") / pl.col("count_prediction_0")).alias("proportion_1_to_0")
    ])
)

# Display the resulting DataFrame
result_df

shape: (288, 4)
┌──────────┬────────────────────┬────────────────────┬───────────────────┐
│ sequence ┆ count_prediction_1 ┆ count_prediction_0 ┆ proportion_1_to_0 │
│ ---      ┆ ---                ┆ ---                ┆ ---               │
│ str      ┆ u32                ┆ u32                ┆ f64               │
╞══════════╪════════════════════╪════════════════════╪═══════════════════╡
│ CAGACTA  ┆ 1290               ┆ 30681              ┆ 0.042046          │
│ ATGACAA  ┆ 87                 ┆ 72419              ┆ 0.001201          │
│ GGGACCC  ┆ 8992               ┆ 83821              ┆ 0.107276          │
│ GTAACAG  ┆ 0                  ┆ 33985              ┆ 0.0               │
│ GAGACTC  ┆ 6887               ┆ 53225              ┆ 0.129394          │
│ …        ┆ …                  ┆ …                  ┆ …                 │
│ CTAACAT  ┆ 0                  ┆ 29203              ┆ 0.0               │
│ AAGACTC  ┆ 4542               ┆ 52859              ┆ 0.085927          │
│ AGGACCA  ┆ 4960               ┆ 75412              ┆ 0.065772          │
│ GGAACTC  ┆ 11292              ┆ 40287              ┆ 0.280289          │
│ GAGACAA  ┆ 222                ┆ 58702              ┆ 0.003782          │
└──────────┴────────────────────┴────────────────────┴───────────────────┘

In [16]:
result_df.write_csv("sequence_prediction_summary.csv")

In [29]:
import plotly.graph_objects as go
import pandas as pd

# Create a DataFrame from the data
data = {
    'Pos 1': [4.06, 3.33, 5.23, 6.45],
    'Pos 2': [1.61, None, 10.15, 2.5],
    'Pos 3': [2.83, None, 6.51, None],
    'Pos 4': [4.79, None, None, None],
    'Pos 5': [None, 4.79, None, None],
    'Pos 6': [1.59, 2.33, None, 10.81],
    'Pos 7': [2.81, 6.25, 5.6, 4.66]
}
index = ['A', 'C', 'G', 'T']
df = pd.DataFrame(data, index=index)

# Create a grouped bar chart
fig = go.Figure()

# Add bars for each nucleotide
for nucleotide in df.index:
    fig.add_trace(go.Bar(
        x=df.columns,
        y=df.loc[nucleotide],
        name=nucleotide
    ))

# Update layout for clarity
fig.update_layout(
    title="Grouped Bar Chart of Values by Nucleotide and Position",
    xaxis_title="Position",
    yaxis_title="Value",
    barmode="group",  # Group bars for each position
    legend_title="Nucleotide",
    width=800,        # Set overall figure width
    height=600  
)

fig.show()


In [31]:
import plotly.graph_objects as go
import pandas as pd

# Data based on the provided table
data = {
    'Pos 1': {'A': 200057, 'C': 100105, 'G': 220595, 'U': 235629},
    'Pos 2': {'A': 97731, 'C': None, 'G': 551444, 'U': 107211},
    'Pos 3': {'A': 209308, 'C': None, 'G': 547078, 'U': None},
    'Pos 4': {'A': 756386, 'C': None, 'G': None, 'U': None},
    'Pos 5': {'A': None, 'C': 756386, 'G': None, 'U': None},
    'Pos 6': {'A': 94448, 'C': 111008, 'G': None, 'U': 550930},
    'Pos 7': {'A': 111127, 'C': 223109, 'G': 215197, 'U': 206953}
}

# Convert data to DataFrame
df = pd.DataFrame(data).fillna(0)  # Fill NaN values with 0

# Define the scientific color palette
scientific_palette = {
    'A': "rgb(31, 119, 180)",   # Blue
    'C': "rgb(255, 127, 14)",   # Orange
    'G': "rgb(44, 160, 44)",    # Green
    'U': "rgb(214, 39, 40)"     # Red
}

# Create the stacked bar chart
fig = go.Figure()

# Add a bar for each nucleotide, stacked at each position
for nucleotide in df.index:
    fig.add_trace(go.Bar(
        x=df.columns,
        y=df.loc[nucleotide],
        name=nucleotide,
        #marker_color=scientific_palette[nucleotide]
    ))

# Update layout for clarity
fig.update_layout(
    title={"text": "Stacked Bar Chart of Modified Nucleotide Counts Across Positions",
    "xanchor": 'center',
    "x": 0.5},
    xaxis_title="Position (7-mer)",
    yaxis_title="Count",
    barmode="stack",  # Stack bars
    legend_title="Nucleotide",
    width=800,        # Set overall figure width
    height=600  
)

fig.show()
